In [82]:
import time
import numpy as np
import pandas as pd
import requests

import json
from pandas.io.json import json_normalize

In [27]:
import _local_settings

In [159]:
# Set ipython's max row display
pd.set_option('display.max_row', 1000)

# Set iPython's max column width to 50
pd.set_option('display.max_columns', 50)

### Get Data Directly from Steam

In [ ]:
ALL_APPS_URL = "http://api.steampowered.com/ISteamApps/GetAppList/v0002/?key=STEAMKEY&format=json"
APP_DETAILS_URL = "http://store.steampowered.com/api/appdetails?appids={APP_ID}"

In [29]:
def get_request(url, parameters=None):
    """Return json-formatted response of a get request using optional parameters.

    Parameters
    ----------
    url : string
    parameters : {'parameter': 'value'}
        parameters to pass as part of get request

    Returns
    -------
    json_data
        json-formatted response (dict-like)
    """
    try:
        response = requests.get(url=url, params=parameters)
    except requests.exceptions.Timeout:
        for i in range(5, 0, -1):
            print('\rTimeout. Waiting... ({})'.format(i), end='')
            time.sleep(1)
        print('\rRetrying.' + ' ' * 10)
        return get_request(url, parameters)
    except requests.exceptions.TooManyRedirects:
        print('TooManyRedirects')
    except requests.exceptions.RequestException as e:
    # catastrophic error. bail.
        raise SystemExit(e)

    if response:
        return response.json()
    else:
        # response is none usually means too many requests. Wait and try again
        print('No response, waiting 10 seconds...')
        time.sleep(10)
        print('Retrying.')
        return get_request(url, parameters)

In [53]:
ALL_APPS_URL = "http://api.steampowered.com/ISteamApps/GetAppList/v0002/?key={STEAMKEY}&format=json".format(STEAMKEY=_local_settings.STEAMKEY)

all_apps = get_request(ALL_APPS_URL)

In [50]:
print(list(all_apps['applist']['apps'])[0:25])

[{'appid': 216938, 'name': 'Pieterw test app76 ( 216938 )'}, {'appid': 660010, 'name': 'test2'}, {'appid': 660130, 'name': 'test3'}, {'appid': 1234450, 'name': 'EDGE OF DAWN'}, {'appid': 1234460, 'name': 'Bernadette and the Demon Circus'}, {'appid': 1234470, 'name': 'Yuhha: Stolen Treasure Demo (English language)'}, {'appid': 1234490, 'name': 'Max Gentlemen Sexy Business! Soundtrack'}, {'appid': 1234510, 'name': 'Aircraft War: Space Wars'}, {'appid': 1234520, 'name': 'The Escaper'}, {'appid': 1234540, 'name': 'Bob Wants to Go Home'}, {'appid': 1234550, 'name': 'Quest Rooms'}, {'appid': 1234570, 'name': 'Episode 1'}, {'appid': 1234580, 'name': 'fullybroKEN - A Unique Post-Apocalyptic RPG'}, {'appid': 1234590, 'name': 'Class Kingdom'}, {'appid': 1234600, 'name': 'Hollow Remnant'}, {'appid': 1234610, 'name': 'BELOW Vol. 3 - Soundtrack'}, {'appid': 1234630, 'name': 'Enemy Gates Stealth War'}, {'appid': 1234680, 'name': 'Volatile'}, {'appid': 1234690, 'name': 'Gotcha'}, {'appid': 1234700, '

In [396]:
def get_app_info(apps):
# needs logic to deal with 200 requests/5 min limits
    count = 0
    loop_count = 0
    failure = 0
    success = 0
    app_data = {}
    app_failure = {}
    for app in apps:
        appid = app['appid']
        count+= 1
        app_info = get_request("http://store.steampowered.com/api/appdetails?appids={APP_ID}".format(APP_ID=appid))
        time.sleep(1.6)  # should keep us below request limit

        if app_info[str(appid)]['success']:
            success += 1
            app_data.update(app_info)
            app_df.to_csv('initial.csv', index=False) 
        else:
            failure += 1
            app_failure.update(app_info)
            app_failure_df.to_csv('app_failure.csv', index=False) 
        
        print(str(count))
        if count > 2000:
            print("reached 2,000 request, stopping")
            break

    print('success: ' + str(success))
    print('failures: ' + str(failure))
    return app_data, app_failure

app_data, app_failure = get_app_info(all_apps['applist']['apps'])

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118


KeyboardInterrupt: 

In [140]:
def convert_to_df(d):
    df = pd.DataFrame.from_dict(d, orient='index')
    df.reset_index(level=0, inplace=True)
    return df

app_df = convert_to_df(app_data)

 

In [142]:
# app_df.to_csv('initial.csv', index=False) 

In [145]:
app_failure_df = convert_to_df(app_failure)
# app_failure_df.to_csv('app_failure.csv', index=False) 

In [141]:
# app_df = pd.read_csv('initial.csv')

# app_df.head()

index  success                                               data
0    579920     True  {'type': 'game', 'name': 'Swatcher', 'steam_ap...
1    579930     True  {'type': 'dlc', 'name': 'Secret World Legends:...
2    579940     True  {'type': 'game', 'name': 'Race for the Galaxy'...
3    579960     True  {'type': 'music', 'name': 'Milkmaid of the Mil...
4    579970     True  {'type': 'demo', 'name': 'Don't Mess Up Demo',...
..      ...      ...                                                ...
938  569685     True  {'type': 'dlc', 'name': 'Toukiden 2 - Armor: I...
939  569686     True  {'type': 'dlc', 'name': 'Toukiden 2 - Armor: F...
940  569687     True  {'type': 'dlc', 'name': 'Toukiden 2 - Mission ...
941  569688     True  {'type': 'dlc', 'name': 'Toukiden 2 - Mission ...
942  569689     True  {'type': 'dlc', 'name': 'Toukiden 2 - Mission ...

[943 rows x 3 columns]

In [143]:
app_df_expanded = pd.concat([app_df.drop(['data'], axis=1), app_df['data'].apply(pd.Series)], axis=1)

In [144]:
app_df_expanded[['type','name','price_overview']]

type                                             name  \
0     game                                         Swatcher   
1      dlc        Secret World Legends: Supernatural Bundle   
2     game                              Race for the Galaxy   
3    music           Milkmaid of the Milky Way - Soundtrack   
4     demo                               Don't Mess Up Demo   
..     ...                                              ...   
938    dlc    Toukiden 2 - Armor: Ibuki Outfit / Oka Outfit   
939    dlc  Toukiden 2 - Armor: Fugaku Outfit / Nagi Outfit   
940    dlc            Toukiden 2 - Mission Collection Set 1   
941    dlc            Toukiden 2 - Mission Collection Set 2   
942    dlc            Toukiden 2 - Mission Collection Set 3   

                                        price_overview  
0    {'currency': 'USD', 'initial': 499, 'final': 4...  
1    {'currency': 'USD', 'initial': 5999, 'final': ...  
2    {'currency': 'USD', 'initial': 699, 'final': 6...  
3    {'currency': 'USD', 'initial': 199, 'final': 1...  
4                                                  NaN  
..                                                 ...  
938  {'currency': 'USD', 'initial': 199, 'final': 1...  
939  {'currency': 'USD', 'initial': 199, 'final': 1...  
940  {'currency': 'USD', 'initial': 499, 'final': 4...  
941  {'currency': 'USD', 'initial': 499, 'final': 4...  
942  {'currency': 'USD', 'initial': 499, 'final': 4...  

[943 rows x 3 columns]

In [160]:
app_df_expanded.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 943 entries, 0 to 942
Data columns (total 41 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   index                    943 non-null    object
 1   success                  943 non-null    bool  
 2   type                     943 non-null    object
 3   name                     943 non-null    object
 4   steam_appid              943 non-null    int64 
 5   required_age             943 non-null    object
 6   is_free                  943 non-null    bool  
 7   detailed_description     943 non-null    object
 8   about_the_game           943 non-null    object
 9   short_description        943 non-null    object
 10  supported_languages      939 non-null    object
 11  header_image             943 non-null    object
 12  website                  527 non-null    object
 13  pc_requirements          943 non-null    object
 14  mac_requirements         943 non-null    o

### Get SteamSpy data - do we really want or need it? - eitherr way we shop rows we don't care about in Steam data...

In [214]:
def get_streamspy_info(apps):
    count = 0
    app_data = []
    url = "https://steamspy.com/api.php"
    
    
    for app in apps:
        count+= 1
        print(app)
        parameters = {"request": "appdetails", "appid": app}
        app_info = get_request(url, parameters)
        time.sleep(.3)  # should keep us below request limit
        app_data.append(app_info)

    print("Found " + str(count) + " apps on SteamSpy.")
    return app_data

sp_app_data = get_streamspy_info(app_df_expanded['index'])

579920
579930
579940
579960
579970
579980
580020
580040
580050
580051
580060
580070
580080
580081
580100
580110
580120
580160
580170
580200
580210
580240
580250
580280
580290
580300
580320
579531
579532
579533
579534
579535
579536
579537
579538
579539
579540
579541
579550
579560
579580
579600
579610
579620
579630
579640
579650
579660
579680
579700
579720
579730
579740
579750
579760
579780
579790
579820
579860
579870
579890
579424
579425
579426
579427
579428
579429
579430
579431
579432
579440
579441
579442
579443
579444
579445
579446
579447
579448
579449
579450
579451
579452
579460
579470
579471
579472
579473
579474
579475
579480
579481
579482
579483
579484
579485
579510
579520
579521
579522
579523
579320
579330
579340
579341
579350
579351
579352
579353
579354
579355
579356
579357
579358
579359
579360
579361
579370
579371
579372
579373
579374
579375
579380
579381
579390
579391
579410
579420
579421
579422
579423
579080
579090
579100
579110
579120
579130
579140
579150
579160
579210
579230

In [231]:
sp_app_data_df = pd.DataFrame(sp_app_data)
# sp_app_data_df.to_csv('steamspy_raw.csv', index=False) 

In [232]:
sp_app_data_df

appid                                               name  \
0    579920                                           Swatcher   
1    579930          Secret World Legends: Supernatural Bundle   
2    579940                                Race for the Galaxy   
3    579960             Milkmaid of the Milky Way - Soundtrack   
4    579970                                 Don't Mess Up Demo   
5    579980                                          Lost Eden   
6    580020                             TEKKEN 7 - Season Pass   
7    580040                                            Formata   
8    580050            RPG Maker MV - Elemental Dungeons Tiles   
9    580051                   RPG Maker MV - Future Steam Punk   
10   580060                                     Cut Cut Buffet   
11   580070                                      Frog Hop Demo   
12   580080         RPG Maker MV - Add-on Vol.3: Train Tileset   
13   580081   RPG Maker MV - Add-on Vol.4: Kid Generator Parts   
14   580100                 Darkest Dungeon: The Crimson Court   
15   580110                                  Abyssal Zone Demo   
16   580120                                Westboro Soundtrack   
17   580160                                  Laraan SoundTrack   
18   580170                                 My Lovely Daughter   
19   580200               Yonder: The Cloud Catcher Chronicles   
20   580210  True Love ~Confide to the maple~Featured Compo...   
21   580240       Fantasy Grounds - More Monsters (Token Pack)   
22   580250                     Crypt of the Serpent King Demo   
23   580280                       Tim Minchin: So F*cking Rock   
24   580290                 Fantasy Grounds - Black Magic (5E)   
25   580300                                 Super Stone Legacy   
26   580320                                           Ashworld   
27   579531  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
28   579532  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
29   579533  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
30   579534  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
31   579535  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
32   579536  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
33   579537  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
34   579538  RTK13WPK - Fan selected Re-Releases Officer Gr...   
35   579539  RTK13WPK - Fan selected Re-Releases Officer Gr...   
36   579540  RTK13WPK - Fan selected Re-Releases Officer Gr...   
37   579541  RTK13WPK - Fan selected Re-Releases Officer Gr...   
38   579550                                    994 W 24th Demo   
39   579560                                         Sky Trader   
40   579580                                 The Source of Evil   
41   579600                           Elephant Express VR Demo   
42   579610                   Gallagher: An Uncensored Evening   
43   579620                        The Body VR: Anatomy Viewer   
44   579630                             Gallagher: The Maddest   
45   579640                     liquivid Video Fisheye Removal   
46   579650                              Root Letter - Artbook   
47   579660                      Gary Gulman: In This Economy?   
48   579680                             Gallagher: Mad As Hell   
49   579700                               Gallagher: Overboard   
50   579720                                           Neverout   
51   579730                            Phoning Home Soundtrack   
52   579740              2Dark Official Soundtrack and Artbook   
53   579750                        Cavern escape - Soundtrack.   
54   579760                    The Journey Down: Chapter Three   
55   579780                                   Mental Asylum VR   
56   579790         Fantasy Grounds - Townsfolk 2 (Token Pack)   
57   579820                              Robinson: The Journey   
58   579860                       Depths of Limbo - Soundtrack   
59   579870                                   

### Play with Steam Data to tease out anything useful / not useful

In [162]:
app_df_expanded.head()

index  success   type                                       name  \
0  579920     True   game                                   Swatcher   
1  579930     True    dlc  Secret World Legends: Supernatural Bundle   
2  579940     True   game                        Race for the Galaxy   
3  579960     True  music     Milkmaid of the Milky Way - Soundtrack   
4  579970     True   demo                         Don't Mess Up Demo   

   steam_appid required_age  is_free  \
0       579920            0    False   
1       579930            0    False   
2       579940            0    False   
3       579960            0    False   
4       579970            0     True   

                                detailed_description  \
0  Swatcher is a color palette creation tool with...   
1  <h1>Secret World Legends</h1><p>Secret World L...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
3  This is the Official Soundtrack for Milkmaid o...   
4  Don't Mess Up is a collection of VR minigames ...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
3  This is the Official Soundtrack for Milkmaid o...   
4  Don't Mess Up is a collection of VR minigames ...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
3  The relaxing and soothing Official Soundtrack ...   
4  Don't Mess Up is a collection of VR minigames ...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
3                                            English   
4  English<strong>*</strong><br><strong>*</strong...   

                                        header_image  \
0  https://steamcdn-a.akamaihd.net/steam/apps/579...   
1  https://steamcdn-a.akamaihd.net/steam/apps/579...   
2  https://steamcdn-a.akamaihd.net/steam/apps/579...   
3  https://steamcdn-a.akamaihd.net/steam/apps/579...   
4  https://steamcdn-a.akamaihd.net/steam/apps/579...   

                           website  \
0           http://swatcherapp.com   
1  https://secretworldlegends.com/   
2      http://templegatesgames.com   
3          http://milkmaidgame.com   
4                             None   

                                     pc_requirements mac_requirements  \
0  {'minimum': '<strong>Minimum:</strong><br><ul ...               []   
1  {'minimum': '<strong>Minimum:</strong><br><ul ...               []   
2  {'minimum': '<strong>Minimum:</strong><br><ul ...               []   
3                                                 []               []   
4                                                 []               []   

  linux_requirements            developers            publishers  \
0                 []        [Frozen Flame]        [Frozen Flame]   
1                 []              [Funcom]              [Funcom]   
2                 []  [Temple Gates Games]  [Temple Gates Games]   
3                 []    [Mattis Folkestad]          [machineboy]   
4                 []            [OKatBest]            [OKatBest]   

                                      price_overview  packages  \
0  {'currency': 'USD', 'initial': 499, 'final': 4...  [148602]   
1  {'currency': 'USD', 'initial': 5999, 'final': ...  [148605]   
2  {'currency': 'USD', 'initial': 699, 'final': 6...  [148608]   
3  {'currency': 'USD', 'initial': 199, 'final': 1...  [148614]   
4                                                NaN       NaN   

                                      package_groups  \
0  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  

In [196]:
app_df_expanded.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 943 entries, 0 to 942
Data columns (total 41 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   index                    943 non-null    object
 1   success                  943 non-null    bool  
 2   type                     943 non-null    object
 3   name                     943 non-null    object
 4   steam_appid              943 non-null    int64 
 5   required_age             943 non-null    object
 6   is_free                  943 non-null    bool  
 7   detailed_description     943 non-null    object
 8   about_the_game           943 non-null    object
 9   short_description        943 non-null    object
 10  supported_languages      939 non-null    object
 11  header_image             943 non-null    object
 12  website                  527 non-null    object
 13  pc_requirements          943 non-null    object
 14  mac_requirements         943 non-null    o

In [202]:
app_df_expanded.drm_notice.unique()


array([nan, 'Denuvo Anti-tamper',
       'Reality Pump DLM V2<br>no machine activation limit',
       'Reality Pump DLM V2'], dtype=object)

### Data modifications to make to Steam Data

(x) remove rows with types not equal to game, dlc or demo  
(x) remove 'index' column and make the steam_appid column the index.  they are always equal. 
(x) remove mac/pc/linux requirements as we can use the platforms column to determine what is supported - dont care about specifics  
(x) change required_age to int type  
(x) need to flatten the price_overview column - are they all formatted the same so I could split it into 2?  
(x) split platforms column into 3 (Windows, Mac, Linux) bool columns  
(x) recommendations should pull out just the number and convert column to int  
(x) convert controller support so bool -> [nan, 'full'] == [False, True]  
(x) convert screenshots to just a counter of number of screenshots  
(x) convert movie to just a counter of number of movies - doesnt look like we can get the movie length from this data (x) split out the genres column so that we can easily access them - probably need to get a list of all genres  
(x) convert release_data to a date, if 'coming_soon==True' set a flag for not release? maybe a new column?  
(x) review column is just one review - not useful so delete  
(x) pull out the appid of the fullgame column so we can link them if needed  
(x) demos is link to appids for game demo - my data sample only has a single demo per game so i just pulled out that id for now - will have to update this code if we find some games with multiple demos
(x) dlc is a list of appids for dlc - kept this column as is an added another column (dlc_count) that is just number of dlc appids

- define the packages and package_group column? list of a numeric?
- look more into content descriptors - i think it relates to age restriction
- split out categories column so they can be easily accessed
- what's achievements?
- what's metacritic?

- find out if drm_notice, ext_user_account_notice mean anything to Kyle?  Short list of values.



(x) columns to remove
    - index
    - header_image
    - pc_requirements
    - mac_requirements
    - linux_requirements
    - support_info
    - background
    - legal notice 
    - reviews 


In [217]:
# set steam_appid as index
app_df_expanded.set_index('steam_appid')

# remove columns we don't care about
cols = ['index',
        'header_image',
        'pc_requirements',
        'mac_requirements',
        'linux_requirements',
        'support_info',
        'background',
        'legal_notice',
        'reviews']

app_df_cleaned_1 = app_df_expanded.drop(columns=cols, axis=1)
app_df_cleaned_1.head()


success   type                                       name  steam_appid  \
0     True   game                                   Swatcher       579920   
1     True    dlc  Secret World Legends: Supernatural Bundle       579930   
2     True   game                        Race for the Galaxy       579940   
3     True  music     Milkmaid of the Milky Way - Soundtrack       579960   
4     True   demo                         Don't Mess Up Demo       579970   

  required_age  is_free                               detailed_description  \
0            0    False  Swatcher is a color palette creation tool with...   
1            0    False  <h1>Secret World Legends</h1><p>Secret World L...   
2            0    False  Explore, Develop, Settle, Trade, Consume, or P...   
3            0    False  This is the Official Soundtrack for Milkmaid o...   
4            0     True  Don't Mess Up is a collection of VR minigames ...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
3  This is the Official Soundtrack for Milkmaid o...   
4  Don't Mess Up is a collection of VR minigames ...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
3  The relaxing and soothing Official Soundtrack ...   
4  Don't Mess Up is a collection of VR minigames ...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
3                                            English   
4  English<strong>*</strong><br><strong>*</strong...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
3          http://milkmaidgame.com    [Mattis Folkestad]   
4                             None            [OKatBest]   

             publishers                                     price_overview  \
0        [Frozen Flame]  {'currency': 'USD', 'initial': 499, 'final': 4...   
1              [Funcom]  {'currency': 'USD', 'initial': 5999, 'final': ...   
2  [Temple Gates Games]  {'currency': 'USD', 'initial': 699, 'final': 6...   
3          [machineboy]  {'currency': 'USD', 'initial': 199, 'final': 1...   
4            [OKatBest]                                                NaN   

   packages                                     package_groups  \
0  [148602]  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [148605]  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [148608]  [{'name': 'default', 'title': 'Buy Race for th...   
3  [148614]  [{'name': 'default', 'title': 'Buy Milkmaid of...   
4       NaN                                                 []   

                                         platforms  \
0  {'windows': True, 'mac': False, 'linux': False}   
1  {'windows': True, 'mac': False, 'linux': False}   
2  {'windows': True, 'mac': False, 'linux': False}   
3   {'windows': True, 'mac': True, 'linux': False}   
4  {'windows': True, 'mac': False, 'linux': False}   

                                              genres  \
0  [{'id': '53', 'description': 'Design & Illustr...   
1  [{'id': '1', 'description': 'Action'}, {'id': ...   
2           [{'id': '2', 'description': 'Strategy'}]   
3  [{'id': '25', 'description': 'Adventure'}, {'i...   
4  [{'id': '1', 'description': 'Action'}, {'id': ...   

                                         screenshots  \
0  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
1  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
2  

In [222]:
# remove rows with types not equal to game, dlc or demo
print(app_df_cleaned_1.type.unique())
valid_type = ['game', 'dlc', 'demo']

contains = [app_df_cleaned_1['type'].str.contains(i) for i in valid_type]
app_df_cleaned_2 = app_df_cleaned_1[np.any(contains, axis=0)]
app_df_cleaned_2.head()
# app_df_cleaned_2 = app_df_cleaned_1[app_df_cleaned_1['type'] == 'music']

['game' 'dlc' 'music' 'demo' 'video' 'episode' 'series']


success  type                                       name  steam_appid  \
0     True  game                                   Swatcher       579920   
1     True   dlc  Secret World Legends: Supernatural Bundle       579930   
2     True  game                        Race for the Galaxy       579940   
4     True  demo                         Don't Mess Up Demo       579970   
5     True  game                                  Lost Eden       579980   

  required_age  is_free                               detailed_description  \
0            0    False  Swatcher is a color palette creation tool with...   
1            0    False  <h1>Secret World Legends</h1><p>Secret World L...   
2            0    False  Explore, Develop, Settle, Trade, Consume, or P...   
4            0     True  Don't Mess Up is a collection of VR minigames ...   
5            0    False  From the makers of Dune™ and Megarace™<br>Lost...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  From the makers of Dune™ and Megarace™<br>Lost...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  An adventure-strategy game in a world never be...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
4  English<strong>*</strong><br><strong>*</strong...   
5  English<strong>*</strong>, Italian, Spanish - ...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
4                             None            [OKatBest]   
5         http://www.interplay.com    [Cryo Interactive]   

             publishers                                     price_overview  \
0        [Frozen Flame]  {'currency': 'USD', 'initial': 499, 'final': 4...   
1              [Funcom]  {'currency': 'USD', 'initial': 5999, 'final': ...   
2  [Temple Gates Games]  {'currency': 'USD', 'initial': 699, 'final': 6...   
4            [OKatBest]                                                NaN   
5           [Interplay]  {'currency': 'USD', 'initial': 999, 'final': 9...   

   packages                                     package_groups  \
0  [148602]  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [148605]  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [148608]  [{'name': 'default', 'title': 'Buy Race for th...   
4       NaN                                                 []   
5  [148620]  [{'name': 'default', 'title': 'Buy Lost Eden',...   

                                         platforms  \
0  {'windows': True, 'mac': False, 'linux': False}   
1  {'windows': True, 'mac': False, 'linux': False}   
2  {'windows': True, 'mac': False, 'linux': False}   
4  {'windows': True, 'mac': False, 'linux': False}   
5  {'windows': True, 'mac': False, 'linux': False}   

                                              genres  \
0  [{'id': '53', 'description': 'Design & Illustr...   
1  [{'id': '1', 'description': 'Action'}, {'id': ...   
2           [{'id': '2', 'description': 'Strategy'}]   
4  [{'id': '1', 'description': 'Action'}, {'id': ...   
5  [{'id': '25', 'description': 'Adventure'}, {'i...   

                                         screenshots  \
0  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
1  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
2  [{'id'

In [234]:
# change required_age to int type

app_df_cleaned_2['required_age'] = pd.to_numeric(app_df_cleaned_2['required_age'])

app_df_cleaned_2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 697 entries, 0 to 942
Data columns (total 33 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   success                  697 non-null    bool  
 1   type                     697 non-null    object
 2   name                     697 non-null    object
 3   steam_appid              697 non-null    int64 
 4   required_age             697 non-null    int64 
 5   is_free                  697 non-null    bool  
 6   detailed_description     697 non-null    object
 7   about_the_game           697 non-null    object
 8   short_description        697 non-null    object
 9   supported_languages      694 non-null    object
 10  website                  503 non-null    object
 11  developers               696 non-null    object
 12  publishers               697 non-null    object
 13  price_overview           569 non-null    object
 14  packages                 573 non-null    o

/Users/emily/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [282]:
# need to flatten the price_overview column - are they all formatted the same so I could split it into 2?

app_df_cleaned_3 = app_df_cleaned_2.copy()

s = app_df_cleaned_3['price_overview'].apply(pd.Series)
s.drop(axis=1, columns=['final_formatted', 'initial_formatted'], inplace=True)
s['final'] = s['final'] / 100
s['initial'] = s['initial'] / 100
s.head()

app_df_cleaned_3 = pd.concat([app_df_cleaned_3, app_df_cleaned_3['price_overview'].apply(pd.Series)], axis=1)
app_df_cleaned_3.drop(axis=1, columns='price_overview', inplace=True)
app_df_cleaned_3.drop(axis=1, columns=[0, 'final_formatted', 'initial_formatted'], inplace=True)
app_df_cleaned_3['final'] = app_df_cleaned_3['final'] / 100
app_df_cleaned_3['initial'] = app_df_cleaned_3['initial'] / 100

app_df_cleaned_3.rename(columns={'currency': 'price_currency',
                                 'discount_percent': 'price_discount_percent', 
                                 'final': 'price_final', 
                                 'initial': 'price_initial',
                                 'recurring_sub': 'price_recurring_sub',
                                 'recurring_sub_desc': 'price_recurring_sub_desc'}, inplace=True)


app_df_cleaned_3.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 697 entries, 0 to 942
Data columns (total 38 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   success                   697 non-null    bool   
 1   type                      697 non-null    object 
 2   name                      697 non-null    object 
 3   steam_appid               697 non-null    int64  
 4   required_age              697 non-null    int64  
 5   is_free                   697 non-null    bool   
 6   detailed_description      697 non-null    object 
 7   about_the_game            697 non-null    object 
 8   short_description         697 non-null    object 
 9   supported_languages       694 non-null    object 
 10  website                   503 non-null    object 
 11  developers                696 non-null    object 
 12  publishers                697 non-null    object 
 13  packages                  573 non-null    object 
 14  package_gr

In [283]:
# Split platforms into 3 bool columns
app_df_cleaned_4 = app_df_cleaned_3.copy()


app_df_cleaned_4 = pd.concat([app_df_cleaned_4, app_df_cleaned_4['platforms'].apply(pd.Series)], axis=1)
app_df_cleaned_4.drop(axis=1, columns='platforms', inplace=True)
app_df_cleaned_4.rename(columns={'windows': 'windows_support', 'mac': 'mac_support', 'linux': 'linux_support'}, inplace=True)
app_df_cleaned_4.head()

success  type                                       name  steam_appid  \
0     True  game                                   Swatcher       579920   
1     True   dlc  Secret World Legends: Supernatural Bundle       579930   
2     True  game                        Race for the Galaxy       579940   
4     True  demo                         Don't Mess Up Demo       579970   
5     True  game                                  Lost Eden       579980   

   required_age  is_free                               detailed_description  \
0             0    False  Swatcher is a color palette creation tool with...   
1             0    False  <h1>Secret World Legends</h1><p>Secret World L...   
2             0    False  Explore, Develop, Settle, Trade, Consume, or P...   
4             0     True  Don't Mess Up is a collection of VR minigames ...   
5             0    False  From the makers of Dune™ and Megarace™<br>Lost...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  From the makers of Dune™ and Megarace™<br>Lost...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  An adventure-strategy game in a world never be...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
4  English<strong>*</strong><br><strong>*</strong...   
5  English<strong>*</strong>, Italian, Spanish - ...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
4                             None            [OKatBest]   
5         http://www.interplay.com    [Cryo Interactive]   

             publishers  packages  \
0        [Frozen Flame]  [148602]   
1              [Funcom]  [148605]   
2  [Temple Gates Games]  [148608]   
4            [OKatBest]       NaN   
5           [Interplay]  [148620]   

                                      package_groups  \
0  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [{'name': 'default', 'title': 'Buy Race for th...   
4                                                 []   
5  [{'name': 'default', 'title': 'Buy Lost Eden',...   

                                              genres  \
0  [{'id': '53', 'description': 'Design & Illustr...   
1  [{'id': '1', 'description': 'Action'}, {'id': ...   
2           [{'id': '2', 'description': 'Strategy'}]   
4  [{'id': '1', 'description': 'Action'}, {'id': ...   
5  [{'id': '25', 'description': 'Adventure'}, {'i...   

                                         screenshots  \
0  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
1  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
2  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
4  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
5  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   

                                              movies  \
0  [{'id': 256677722, 'name': 'Swatcher Demonstra...   
1  [{'id': 256691734, 'name': 'Trailer', 'thumbna...   
2  [{'id': 256687045, 'name': 'Race for the Galax...   
4                                                NaN   
5  [{'id': 256679159, 'name': 'game play trailer'...   

                                     release_date         content_descriptors  \
0  {'coming_soon': False, 'date': 'Jan 13, 2017

In [301]:
# recommendations should pull out just the number and convert column to int
app_df_cleaned_5 = app_df_cleaned_4.copy()

app_df_cleaned_5 = pd.concat([app_df_cleaned_5, app_df_cleaned_5['recommendations'].apply(pd.Series)], axis=1)
app_df_cleaned_5.drop(axis=1, columns=[0, 'recommendations'], inplace=True)
app_df_cleaned_5.rename(columns={'total': 'recommendations'}, inplace=True)
app_df_cleaned_5.head()

success  type                                       name  steam_appid  \
0     True  game                                   Swatcher       579920   
1     True   dlc  Secret World Legends: Supernatural Bundle       579930   
2     True  game                        Race for the Galaxy       579940   
4     True  demo                         Don't Mess Up Demo       579970   
5     True  game                                  Lost Eden       579980   

   required_age  is_free                               detailed_description  \
0             0    False  Swatcher is a color palette creation tool with...   
1             0    False  <h1>Secret World Legends</h1><p>Secret World L...   
2             0    False  Explore, Develop, Settle, Trade, Consume, or P...   
4             0     True  Don't Mess Up is a collection of VR minigames ...   
5             0    False  From the makers of Dune™ and Megarace™<br>Lost...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  From the makers of Dune™ and Megarace™<br>Lost...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  An adventure-strategy game in a world never be...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
4  English<strong>*</strong><br><strong>*</strong...   
5  English<strong>*</strong>, Italian, Spanish - ...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
4                             None            [OKatBest]   
5         http://www.interplay.com    [Cryo Interactive]   

             publishers  packages  \
0        [Frozen Flame]  [148602]   
1              [Funcom]  [148605]   
2  [Temple Gates Games]  [148608]   
4            [OKatBest]       NaN   
5           [Interplay]  [148620]   

                                      package_groups  \
0  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [{'name': 'default', 'title': 'Buy Race for th...   
4                                                 []   
5  [{'name': 'default', 'title': 'Buy Lost Eden',...   

                                              genres  \
0  [{'id': '53', 'description': 'Design & Illustr...   
1  [{'id': '1', 'description': 'Action'}, {'id': ...   
2           [{'id': '2', 'description': 'Strategy'}]   
4  [{'id': '1', 'description': 'Action'}, {'id': ...   
5  [{'id': '25', 'description': 'Adventure'}, {'i...   

                                         screenshots  \
0  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
1  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
2  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
4  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
5  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   

                                              movies  \
0  [{'id': 256677722, 'name': 'Swatcher Demonstra...   
1  [{'id': 256691734, 'name': 'Trailer', 'thumbna...   
2  [{'id': 256687045, 'name': 'Race for the Galax...   
4                                                NaN   
5  [{'id': 256679159, 'name': 'game play trailer'...   

                                     release_date         content_descriptors  \
0  {'coming_soon': False, 'date': 'Jan 13, 2017

In [320]:
# convert controller support so bool
app_df_cleaned_6 = app_df_cleaned_5.copy()

app_df_cleaned_6['controller_support'] = app_df_cleaned_6['controller_support'].map({np.nan: False, 'full': True})
app_df_cleaned_6.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 697 entries, 0 to 942
Data columns (total 40 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   success                   697 non-null    bool   
 1   type                      697 non-null    object 
 2   name                      697 non-null    object 
 3   steam_appid               697 non-null    int64  
 4   required_age              697 non-null    int64  
 5   is_free                   697 non-null    bool   
 6   detailed_description      697 non-null    object 
 7   about_the_game            697 non-null    object 
 8   short_description         697 non-null    object 
 9   supported_languages       694 non-null    object 
 10  website                   503 non-null    object 
 11  developers                696 non-null    object 
 12  publishers                697 non-null    object 
 13  packages                  573 non-null    object 
 14  package_gr

In [323]:
# convert screenshots and movie to just a counter of number of movies 
# doesnt look like we can get the movie length from this data

def replace_with_count(df, col):
    df = pd.concat([df, df[col].str.len()], axis=1)
    # this results in both old and new columns having the same name 
    # so below code will remove the old screenshots dictionary column
    df = df.loc[:,~df.columns.duplicated(keep='last')]
    return df

app_df_cleaned_7 = app_df_cleaned_6.copy()

app_df_cleaned_7 = replace_with_count(app_df_cleaned_7, 'screenshots')
app_df_cleaned_7.rename(columns={'screenshots': 'screenshot_count'}, inplace=True)


app_df_cleaned_7 = replace_with_count(app_df_cleaned_7, 'movies')
app_df_cleaned_7.rename(columns={'movies': 'movie_count'}, inplace=True)

app_df_cleaned_7.head()

success  type                                       name  steam_appid  \
0     True  game                                   Swatcher       579920   
1     True   dlc  Secret World Legends: Supernatural Bundle       579930   
2     True  game                        Race for the Galaxy       579940   
4     True  demo                         Don't Mess Up Demo       579970   
5     True  game                                  Lost Eden       579980   

   required_age  is_free                               detailed_description  \
0             0    False  Swatcher is a color palette creation tool with...   
1             0    False  <h1>Secret World Legends</h1><p>Secret World L...   
2             0    False  Explore, Develop, Settle, Trade, Consume, or P...   
4             0     True  Don't Mess Up is a collection of VR minigames ...   
5             0    False  From the makers of Dune™ and Megarace™<br>Lost...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  From the makers of Dune™ and Megarace™<br>Lost...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  An adventure-strategy game in a world never be...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
4  English<strong>*</strong><br><strong>*</strong...   
5  English<strong>*</strong>, Italian, Spanish - ...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
4                             None            [OKatBest]   
5         http://www.interplay.com    [Cryo Interactive]   

             publishers  packages  \
0        [Frozen Flame]  [148602]   
1              [Funcom]  [148605]   
2  [Temple Gates Games]  [148608]   
4            [OKatBest]       NaN   
5           [Interplay]  [148620]   

                                      package_groups  \
0  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [{'name': 'default', 'title': 'Buy Race for th...   
4                                                 []   
5  [{'name': 'default', 'title': 'Buy Lost Eden',...   

                                              genres  \
0  [{'id': '53', 'description': 'Design & Illustr...   
1  [{'id': '1', 'description': 'Action'}, {'id': ...   
2           [{'id': '2', 'description': 'Strategy'}]   
4  [{'id': '1', 'description': 'Action'}, {'id': ...   
5  [{'id': '25', 'description': 'Adventure'}, {'i...   

                                     release_date         content_descriptors  \
0  {'coming_soon': False, 'date': 'Jan 13, 2017'}  {'ids': [], 'notes': None}   
1  {'coming_soon': False, 'date': 'Jul 31, 2017'}  {'ids': [], 'notes': None}   
2  {'coming_soon': False, 'date': 'Jun 27, 2017'}  {'ids': [], 'notes': None}   
4  {'coming_soon': False, 'date': 'Jan 13, 2017'}  {'ids': [], 'notes': None}   
5  {'coming_soon': False, 'date': 'Feb 13, 2017'}  {'ids': [], 'notes': None}   

                                            fullgame  \
0                                                NaN   
1  {'appid': '215280', 'name': 'Secret World Lege...   
2                                                NaN   
4       {'appid': '575170', 'name': 'Don't Mess Up'}   
5                                  

In [392]:
# split out the genres column so that we can easily access them - probably need to get a list of all genres
app_df_cleaned_8 = app_df_cleaned_7.copy()

#first we need to create a table of all possible values then figure out how to store those so we can access them
s = app_df_cleaned_8['genres'].apply(pd.Series)
# combine everything into single column
y = s[0].append([s[1],s[2],s[3],s[4],s[5],s[6],s[7],s[8],s[9]],ignore_index=True).dropna()
#split out dict to seprate columns
z = y.apply(pd.Series)
z = z.drop_duplicates(subset=['id','description'], keep="first")

# create a column for each unique genre and then fill those columns in the df with bools
for index, row in z.iterrows():
    no_space_name = row['description'].replace(" ", "_")
    new_col = 'genre_{}'.format(no_space_name)
    app_df_cleaned_8[new_col] = False

for index, row in app_df_cleaned_8.iterrows():
    if type(row['genres']) == float:
        continue
    for item in row['genres']:
        no_space_name = item['description'].replace(" ", "_")
        new_name = 'genre_{}'.format(no_space_name)
        row[new_name] = True
app_df_cleaned_8

success  type                                               name  \
0       True  game                                           Swatcher   
1       True   dlc          Secret World Legends: Supernatural Bundle   
2       True  game                                Race for the Galaxy   
4       True  demo                                 Don't Mess Up Demo   
5       True  game                                          Lost Eden   
6       True   dlc                             TEKKEN 7 - Season Pass   
7       True  game                                            Formata   
8       True   dlc            RPG Maker MV - Elemental Dungeons Tiles   
9       True   dlc                   RPG Maker MV - Future Steam Punk   
10      True  game                                     Cut Cut Buffet   
11      True  demo                                      Frog Hop Demo   
12      True   dlc         RPG Maker MV - Add-on Vol.3: Train Tileset   
13      True   dlc   RPG Maker MV - Add-on Vol.4: Kid Generator Parts   
14      True   dlc                Darkest Dungeon®: The Crimson Court   
15      True  demo                                  Abyssal Zone Demo   
16      True   dlc                                Westboro Soundtrack   
17      True   dlc                                  Laraan SoundTrack   
18      True  game                                 My Lovely Daughter   
19      True  game               Yonder: The Cloud Catcher Chronicles   
20      True   dlc                                  真恋～寄语枫秋～特色作曲家（秋石）   
21      True   dlc       Fantasy Grounds - More Monsters (Token Pack)   
22      True  demo                     Crypt of the Serpent King Demo   
24      True   dlc                 Fantasy Grounds - Black Magic (5E)   
25      True  game                                 Super Stone Legacy   
26      True  game                                           Ashworld   
27      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
28      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
29      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
30      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
31      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
32      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
33      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
34      True   dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...   
35      True   dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...   
36      True   dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...   
37      True   dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...   
38      True  demo                                    994 W 24th Demo   
39      True  game                                         Sky Trader   
40      True  game                                 The Source of Evil   
41      True  demo                           Elephant Express VR Demo   
43      True  game                        The Body VR: Anatomy Viewer   
45      True  game                     liquivid Video Fisheye Removal   
46      True   dlc                              Root Letter - Artbook   
50      True  game                                           Neverout   
51      True   dlc                            Phoning Home Soundtrack   
52      True   dlc              2Dark Official Soundtrack and Artbook   
53      True   dlc                        Cavern escape - Soundtrack.   
54      True  game                    The Journey Down: Chapter Three   
55      True  game                                   Mental Asylum VR   
56      True   dlc         Fantasy Grounds - Townsfolk 2 (Token Pack)   
57      True  game                              Robinson: The Journey   
58      True   dlc                       Depths of Limbo - Soundtrack   
59      True  game                                       Biosupremacy   
60      True   dlc            The Mooseman Soundtrack and Artbo

In [406]:
# convert release_data to a date, if 'coming_soon==True' set a flag for not release? maybe a new column?

app_df_cleaned_9 = app_df_cleaned_8.copy()

s = app_df_cleaned_9['release_date'].apply(pd.Series)
s['date'] = pd.to_datetime(s['date'], errors='coerce')

app_df_cleaned_9 = pd.concat([app_df_cleaned_9, s], axis=1)
app_df_cleaned_9.drop(axis=1, columns='release_date', inplace=True)
app_df_cleaned_9.rename(columns={'date': 'release_date'}, inplace=True)
app_df_cleaned_9.head()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 697 entries, 0 to 942
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   coming_soon  697 non-null    bool          
 1   date         687 non-null    datetime64[ns]
dtypes: bool(1), datetime64[ns](1)
memory usage: 11.6 KB


success  type                                       name  steam_appid  \
0     True  game                                   Swatcher       579920   
1     True   dlc  Secret World Legends: Supernatural Bundle       579930   
2     True  game                        Race for the Galaxy       579940   
4     True  demo                         Don't Mess Up Demo       579970   
5     True  game                                  Lost Eden       579980   

   required_age  is_free                               detailed_description  \
0             0    False  Swatcher is a color palette creation tool with...   
1             0    False  <h1>Secret World Legends</h1><p>Secret World L...   
2             0    False  Explore, Develop, Settle, Trade, Consume, or P...   
4             0     True  Don't Mess Up is a collection of VR minigames ...   
5             0    False  From the makers of Dune™ and Megarace™<br>Lost...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  From the makers of Dune™ and Megarace™<br>Lost...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  An adventure-strategy game in a world never be...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
4  English<strong>*</strong><br><strong>*</strong...   
5  English<strong>*</strong>, Italian, Spanish - ...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
4                             None            [OKatBest]   
5         http://www.interplay.com    [Cryo Interactive]   

             publishers  packages  \
0        [Frozen Flame]  [148602]   
1              [Funcom]  [148605]   
2  [Temple Gates Games]  [148608]   
4            [OKatBest]       NaN   
5           [Interplay]  [148620]   

                                      package_groups  \
0  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [{'name': 'default', 'title': 'Buy Race for th...   
4                                                 []   
5  [{'name': 'default', 'title': 'Buy Lost Eden',...   

                                              genres  \
0  [{'id': '53', 'description': 'Design & Illustr...   
1  [{'id': '1', 'description': 'Action'}, {'id': ...   
2           [{'id': '2', 'description': 'Strategy'}]   
4  [{'id': '1', 'description': 'Action'}, {'id': ...   
5  [{'id': '25', 'description': 'Adventure'}, {'i...   

          content_descriptors  \
0  {'ids': [], 'notes': None}   
1  {'ids': [], 'notes': None}   
2  {'ids': [], 'notes': None}   
4  {'ids': [], 'notes': None}   
5  {'ids': [], 'notes': None}   

                                            fullgame  \
0                                                NaN   
1  {'appid': '215280', 'name': 'Secret World Lege...   
2                                                NaN   
4       {'appid': '575170', 'name': 'Don't Mess Up'}   
5                                                NaN   

                                          categories  \
0                                                NaN   
1  [{'id': 1, 'description': 'Multi-player'}, {'i...   
2  [{'id': 2, 'description': 'Single-player'}, {'...   
4  [{'id': 2, 'description': 'Single-playe

In [414]:
# how long is reviews column - most have none - can maybe trash this

app_df_cleaned_10 = app_df_cleaned_9.copy()
print(app_df_cleaned_10.info())
app_df_cleaned_10.drop(columns='reviews', inplace=True)
print(app_df_cleaned_10.info())

# note that i already added reviews column to list of columns to delete in the begining


<class 'pandas.core.frame.DataFrame'>
Int64Index: 697 entries, 0 to 942
Data columns (total 66 columns):
 #   Column                       Non-Null Count  Dtype         
---  ------                       --------------  -----         
 0   success                      697 non-null    bool          
 1   type                         697 non-null    object        
 2   name                         697 non-null    object        
 3   steam_appid                  697 non-null    int64         
 4   required_age                 697 non-null    int64         
 5   is_free                      697 non-null    bool          
 6   detailed_description         697 non-null    object        
 7   about_the_game               697 non-null    object        
 8   short_description            697 non-null    object        
 9   supported_languages          694 non-null    object        
 10  website                      503 non-null    object        
 11  developers                   696 non-null    

In [484]:
# - pull out the appid of the fullgame column so we can link them if needed
# - demos is link to appids for game demo - probably do care about this - maybe convert to a true/false for demo existing? maybe a column for nbr demos?
# - dlc is a list of appids for dlc - lets add a column for the dlc count
app_df_cleaned_11 = app_df_cleaned_10.copy()

fullgame = app_df_cleaned_11['fullgame']
s = fullgame.apply(pd.Series)
s.drop(axis=1, columns=['name', 0], inplace=True)
s.rename(columns={'appid': 'fullgame_appid'}, inplace=True)
app_df_cleaned_11 = pd.concat([app_df_cleaned_11, s], axis=1)

# there seems to be only 1 demo in the subset i pulled so we'll just show that one demo id instead of the dict
s = app_df_cleaned_11['demos'].apply(pd.Series)
y = pd.Series()
s['demo_appid'] = s[0].apply(lambda x: str(x['appid']) if not pd.isnull(x) else np.nan)
app_df_cleaned_11 = pd.concat([app_df_cleaned_11, s['demo_appid']], axis=1)

# let's keep the list of dlc appid incase we want them
app_df_cleaned_11['dlc_count'] = app_df_cleaned_11['dlc'].apply(lambda x: len(x) if type(x) == list else 0)
app_df_cleaned_11


success  type                                               name  \
0       True  game                                           Swatcher   
1       True   dlc          Secret World Legends: Supernatural Bundle   
2       True  game                                Race for the Galaxy   
4       True  demo                                 Don't Mess Up Demo   
5       True  game                                          Lost Eden   
6       True   dlc                             TEKKEN 7 - Season Pass   
7       True  game                                            Formata   
8       True   dlc            RPG Maker MV - Elemental Dungeons Tiles   
9       True   dlc                   RPG Maker MV - Future Steam Punk   
10      True  game                                     Cut Cut Buffet   
11      True  demo                                      Frog Hop Demo   
12      True   dlc         RPG Maker MV - Add-on Vol.3: Train Tileset   
13      True   dlc   RPG Maker MV - Add-on Vol.4: Kid Generator Parts   
14      True   dlc                Darkest Dungeon®: The Crimson Court   
15      True  demo                                  Abyssal Zone Demo   
16      True   dlc                                Westboro Soundtrack   
17      True   dlc                                  Laraan SoundTrack   
18      True  game                                 My Lovely Daughter   
19      True  game               Yonder: The Cloud Catcher Chronicles   
20      True   dlc                                  真恋～寄语枫秋～特色作曲家（秋石）   
21      True   dlc       Fantasy Grounds - More Monsters (Token Pack)   
22      True  demo                     Crypt of the Serpent King Demo   
24      True   dlc                 Fantasy Grounds - Black Magic (5E)   
25      True  game                                 Super Stone Legacy   
26      True  game                                           Ashworld   
27      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
28      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
29      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
30      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
31      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
32      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
33      True   dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...   
34      True   dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...   
35      True   dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...   
36      True   dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...   
37      True   dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...   
38      True  demo                                    994 W 24th Demo   
39      True  game                                         Sky Trader   
40      True  game                                 The Source of Evil   
41      True  demo                           Elephant Express VR Demo   
43      True  game                        The Body VR: Anatomy Viewer   
45      True  game                     liquivid Video Fisheye Removal   
46      True   dlc                              Root Letter - Artbook   
50      True  game                                           Neverout   
51      True   dlc                            Phoning Home Soundtrack   
52      True   dlc              2Dark Official Soundtrack and Artbook   
53      True   dlc                        Cavern escape - Soundtrack.   
54      True  game                    The Journey Down: Chapter Three   
55      True  game                                   Mental Asylum VR   
56      True   dlc         Fantasy Grounds - Townsfolk 2 (Token Pack)   
57      True  game                              Robinson: The Journey   
58      True   dlc                       Depths of Limbo - Soundtrack   
59      True  game                                       Biosupremacy   
60      True   dlc            The Mooseman Soundtrack and Artbo